# Training a Linear Regression Model to Predict GPU Performance 

Welcome to our programming project! This is where you'll get to apply the knowledge you obtained in class on a real world project. While the demos are done using SKLearn for simplicity, these programming projects aim to expose you to PyTorch, an industrial library for Machine Learning.


## Introduction

The GPU is a piece of computing hardware first developed in the early 1990s for accelerating graphical applications. Due to its highly parallel nature, people eventually found great uses of GPUs in areas other than gaming. Today, the GPU market is a 20 billion dollar market that serves the fields of video games, AI, crypto, scientific computing and engineering sectors.

In this project, we will train a linear regression model on a GPU dataset -- our goal is to build a web application that takes in the **process node, die area, memory size,** and the number of **millions of transistors** to predict the **compute performance** of that GPU.

## Importing the Necessary Libraries

This project aims to train a linear regression model on the **AMD Radeon and Nvidia GPU Specifications** dataset by  JetBrains Datalore. Here are a list of libraries used in this project:

- **PyTorch**: A powerful machine learning Library
- **PyTorch Lightning**: We only use it for its R2score function
- **Pandas** and **Numpy**: Used for easy data storage and linear algebra
- **SKLearn**: Train test split 
- **Matplotlib** and **Bokeh**: For creating static and dynamic visualizations

In [1]:
import torch
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import PolynomialFeatures
from bokeh.plotting import show, figure, output_notebook


pd.set_option('display.max_colwidth', None)

## Loading the Dataset

The first step is to load and visualize the  dataset. This is crucial in any machine learning development process, as this can give you an idea of what features to include or exclude.

In [2]:
gpu_dataset = pd.read_csv("datasets/gpus_v2.csv")
gpu_dataset = gpu_dataset.sample(frac=1).reset_index(drop=True)
gpu_dataset.head(30)

Manufacturer        Class                        Name  Year  Fab  \
0        Nvidia  Workstation                Quadro M5000  2015   28   
1    AMD Radeon  Workstation                 FireMV 2260  2008   55   
2        Nvidia   Datacenter                    GRID M40  2016   28   
3    AMD Radeon      Desktop                 Radeon 550X  2018   14   
4    AMD Radeon      Desktop  Radeon HD 7870 GHz Edition  2012   28   
5        Nvidia      Desktop              GeForce GT 320  2010   40   
6        Nvidia      Desktop           GeForce 9800 GTX+  2008   55   
7    AMD Radeon  Workstation               FirePro V5900  2011   40   
8        Nvidia      Desktop              GeForce GT 710  2016   28   
9        Nvidia   Datacenter                  Tesla C870  2007   90   
10       Nvidia   Datacenter                  GRID K260Q  2013   28   
11       Nvidia      Desktop              GeForce GT 740  2014   28   
12       Nvidia      Desktop                 GeForce 210  2009   40   
13   AMD Radeon      Desktop              Radeon HD 5750  2009   40   
14   AMD Radeon      Desktop              Radeon HD 5850  2009   40   
15   AMD Radeon   Datacenter             FireStream 9250  2008   55   
16   AMD Radeon      Desktop              Radeon HD 5670  2010   40   
17       Nvidia  Workstation             Quadro RTX 5000  2018   12   
18   AMD Radeon      Desktop              Radeon HD 4870  2008   55   
19   AMD Radeon      Desktop              Radeon R7 250X  2014   28   
20       Nvidia      Desktop             GeForce GTS 295  2009   55   
21       Nvidia      Desktop    GeForce GTX 650 Ti Boost  2013   28   
22       Nvidia   Datacenter                   GRID A100  2020    7   
23       Nvidia  Workstation                Quadro P4000  2017   16   
24       Nvidia  Workstation               Quadro FX 580  2009   55   
25   AMD Radeon      Desktop              Radeon HD 4810  2009   55   
26       Nvidia      Desktop              GeForce GT 530  2011   40   
27   AMD Radeon  Workstation               FirePro W7000  2012   28   
28   AMD Radeon  Workstation             Radeon Pro 5700  2020    7   
29       Nvidia   Datacenter                    Tesla P6  2017   16   

    Transistors (mln)  Die size  Memory size  Memory speed    GFLOPS    TDP  
0                5200       398         8192        211.60   4252.00  150.0  
1                 181        67          256          8.00     48.00   15.0  
2                1870       148         8192         83.20    793.30   50.0  
3                2200       101         4096         56.00   1647.00   50.0  
4                2800       212         2048        153.60   1000.00  175.0  
5                 727       144         1024         25.30    187.50   43.0  
6                 754       260         1024         70.40    470.00  141.0  
7                2640       389         2048         64.00    614.40   75.0  
8                1020        79         2048         40.00    366.00   19.0  
9                 681       484         1536         76.80    345.60  171.0  
10               3540       294         2048        160.00   2289.00  225.0  
11               1270       118         4096         80.10    762.60   64.0  
12                260        57         1024         12.80     44.90   30.5  
13               1040       170         1024         73.60   1008.00   86.0  
14               2154       334         2048        128.00   2088.00  151.0  
15                956       256         1024         63.55   1000.00  150.0  
16                627       104         2048         64.00    620.00   64.0  
17              13600       545        16384        448.00  11150.00  230.0  
18                956       256         2048        115.20   1200.00  150.0  
19               1500       123         2048         72.00   1280.00   95.0  
20               2800       940         1792        223.80   1192.30  289.0  
21               2540       221         2048        144.20   1505.28  134.0  
22     

Here, we are going to choose the columns `Transistors (mln)`, `Die size`, `Memory size` and `Fab` to be our **training features** and `GFLOPS` to be our **labels**.

In [3]:
# Creating np.arrays containing our training features and labels
features = gpu_dataset[["Transistors (mln)", "Die size", "Memory size", "Fab"]].to_numpy()
labels = gpu_dataset[['GFLOPS']].to_numpy()

print(f"features shape: {features.shape}")
print(f"labels shape: {labels.shape}\n")

# Train test split
X_train, X_test, Y_train, Y_test = train_test_split(features, labels, test_size=0.1)


print(f"X_train shape: {X_train.shape}")
print(f"Y_train shape: {Y_train.shape}")
print(f"X_test shape: {X_test.shape}")
print(f"Y_test shape: {Y_test.shape}")


features shape: (497, 4)
labels shape: (497, 1)

X_train shape: (447, 4)
Y_train shape: (447, 1)
X_test shape: (50, 4)
Y_test shape: (50, 1)


## Prototyping Our First Model (Multi-variate Linear Regression)

Our first model is going to perform Multi-variate linear regression on the data. In PyTorch, we actually have to define our own class (which is a subclass of torch.nn.Module) as well as its `forward()` function.

In [4]:
from torch.nn import Module, MSELoss, Linear
from torch.optim import SGD

class Linreg(Module):
    def __init__(self, inputs, outputs):
        super().__init__()
        """
        Args:
            inputs (int): the input dimensions
            outputs (int): the output dimensions
        """
        
        self.linear = Linear(inputs, outputs)      
        
    def forward(self, x):
        """
        The forward propagation method. This method is used
        by the torch.nn.Module subclass when training or evaluating
        """
        y_pred = self.linear(x)
        return y_pred
    

In [5]:
input_dims, output_dims = (X_train.shape[1], Y_train.shape[1])

# Epochs is the number of passes over our training set
learning_rate = 0.000000005
epochs = 50000

In [6]:
model = Linreg(input_dims, output_dims)

# Optimizing algorithm and loss (optimizing criterion)
optimizer = SGD(model.parameters(), lr=learning_rate)
loss = MSELoss()

In [7]:
inputs = Variable(torch.from_numpy(X_train)).float()
labels = Variable(torch.from_numpy(Y_train)).float()

# We need to import certain elements of this notebook 
# into a python file. if __name__ == "__main__" prevents these
# sections from running when importing, as it is computationally
# expensive
if __name__ == "__main__":
    for i in range(epochs):
        
        # clears gradient buffer from previous iteration
        model.zero_grad()
        # Feed forward
        pred = model(inputs)
        # Calcluate errors
        errors = loss(pred, labels)
        print(f"loss of iteration {i+1}: {errors}")
        # Backpropagation
        errors.backward()
        # update parameters
        optimizer.step()
    
    

loss of iteration 1: 9936294.0
loss of iteration 2: 7666032.5
loss of iteration 3: 6731890.5
loss of iteration 4: 6335704.0
loss of iteration 5: 6158237.5
loss of iteration 6: 6071431.5
loss of iteration 7: 6023602.0
loss of iteration 8: 5993634.5
loss of iteration 9: 5972693.5
loss of iteration 10: 5956922.5
loss of iteration 11: 5944497.5
loss of iteration 12: 5934467.0
loss of iteration 13: 5926261.5
loss of iteration 14: 5919499.0
loss of iteration 15: 5913899.0
loss of iteration 16: 5909246.5
loss of iteration 17: 5905369.5
loss of iteration 18: 5902128.5
loss of iteration 19: 5899410.5
loss of iteration 20: 5897122.0
loss of iteration 21: 5895185.0
loss of iteration 22: 5893539.0
loss of iteration 23: 5892131.5
loss of iteration 24: 5890919.5
loss of iteration 25: 5889868.0
loss of iteration 26: 5888950.5
loss of iteration 27: 5888142.0
loss of iteration 28: 5887423.5
loss of iteration 29: 5886778.0
loss of iteration 30: 5886192.5
loss of iteration 31: 5885659.0
loss of iteration

loss of iteration 348: 5802765.5
loss of iteration 349: 5802549.5
loss of iteration 350: 5802332.0
loss of iteration 351: 5802117.0
loss of iteration 352: 5801900.5
loss of iteration 353: 5801685.0
loss of iteration 354: 5801471.0
loss of iteration 355: 5801256.0
loss of iteration 356: 5801041.5
loss of iteration 357: 5800826.0
loss of iteration 358: 5800612.5
loss of iteration 359: 5800397.5
loss of iteration 360: 5800184.5
loss of iteration 361: 5799970.5
loss of iteration 362: 5799757.5
loss of iteration 363: 5799544.5
loss of iteration 364: 5799331.0
loss of iteration 365: 5799118.5
loss of iteration 366: 5798905.0
loss of iteration 367: 5798694.0
loss of iteration 368: 5798481.5
loss of iteration 369: 5798270.0
loss of iteration 370: 5798058.0
loss of iteration 371: 5797847.0
loss of iteration 372: 5797636.0
loss of iteration 373: 5797425.5
loss of iteration 374: 5797214.5
loss of iteration 375: 5797004.5
loss of iteration 376: 5796794.0
loss of iteration 377: 5796583.0
loss of it

loss of iteration 929: 5709250.0
loss of iteration 930: 5709134.0
loss of iteration 931: 5709018.0
loss of iteration 932: 5708903.0
loss of iteration 933: 5708787.0
loss of iteration 934: 5708671.5
loss of iteration 935: 5708557.0
loss of iteration 936: 5708442.0
loss of iteration 937: 5708326.5
loss of iteration 938: 5708211.5
loss of iteration 939: 5708097.5
loss of iteration 940: 5707982.5
loss of iteration 941: 5707867.5
loss of iteration 942: 5707753.5
loss of iteration 943: 5707638.5
loss of iteration 944: 5707525.0
loss of iteration 945: 5707410.5
loss of iteration 946: 5707297.0
loss of iteration 947: 5707183.0
loss of iteration 948: 5707069.5
loss of iteration 949: 5706956.0
loss of iteration 950: 5706843.0
loss of iteration 951: 5706729.5
loss of iteration 952: 5706616.5
loss of iteration 953: 5706504.0
loss of iteration 954: 5706390.0
loss of iteration 955: 5706278.0
loss of iteration 956: 5706165.0
loss of iteration 957: 5706052.0
loss of iteration 958: 5705940.5
loss of it

loss of iteration 1766: 5645068.0
loss of iteration 1767: 5645020.0
loss of iteration 1768: 5644972.0
loss of iteration 1769: 5644925.5
loss of iteration 1770: 5644877.5
loss of iteration 1771: 5644830.0
loss of iteration 1772: 5644783.0
loss of iteration 1773: 5644735.5
loss of iteration 1774: 5644688.5
loss of iteration 1775: 5644641.0
loss of iteration 1776: 5644594.5
loss of iteration 1777: 5644546.5
loss of iteration 1778: 5644500.0
loss of iteration 1779: 5644452.5
loss of iteration 1780: 5644405.5
loss of iteration 1781: 5644358.5
loss of iteration 1782: 5644312.0
loss of iteration 1783: 5644264.5
loss of iteration 1784: 5644218.5
loss of iteration 1785: 5644171.0
loss of iteration 1786: 5644124.0
loss of iteration 1787: 5644078.5
loss of iteration 1788: 5644031.5
loss of iteration 1789: 5643985.0
loss of iteration 1790: 5643938.5
loss of iteration 1791: 5643892.5
loss of iteration 1792: 5643845.5
loss of iteration 1793: 5643799.0
loss of iteration 1794: 5643753.0
loss of iterat

loss of iteration 2518: 5620207.0
loss of iteration 2519: 5620184.5
loss of iteration 2520: 5620162.5
loss of iteration 2521: 5620140.0
loss of iteration 2522: 5620118.5
loss of iteration 2523: 5620097.0
loss of iteration 2524: 5620075.5
loss of iteration 2525: 5620054.0
loss of iteration 2526: 5620031.0
loss of iteration 2527: 5620009.0
loss of iteration 2528: 5619988.5
loss of iteration 2529: 5619966.5
loss of iteration 2530: 5619945.0
loss of iteration 2531: 5619924.0
loss of iteration 2532: 5619901.5
loss of iteration 2533: 5619880.5
loss of iteration 2534: 5619858.5
loss of iteration 2535: 5619836.5
loss of iteration 2536: 5619815.0
loss of iteration 2537: 5619794.0
loss of iteration 2538: 5619772.0
loss of iteration 2539: 5619750.5
loss of iteration 2540: 5619728.5
loss of iteration 2541: 5619707.0
loss of iteration 2542: 5619687.5
loss of iteration 2543: 5619665.0
loss of iteration 2544: 5619644.0
loss of iteration 2545: 5619622.5
loss of iteration 2546: 5619601.0
loss of iterat

...

loss of iteration 46593: 5546457.0
loss of iteration 46594: 5546457.0
loss of iteration 46595: 5546456.0
loss of iteration 46596: 5546455.0
loss of iteration 46597: 5546454.0
loss of iteration 46598: 5546453.5
loss of iteration 46599: 5546452.0
loss of iteration 46600: 5546451.5
loss of iteration 46601: 5546451.5
loss of iteration 46602: 5546449.5
loss of iteration 46603: 5546449.0
loss of iteration 46604: 5546447.5
loss of iteration 46605: 5546446.5
loss of iteration 46606: 5546445.5
loss of iteration 46607: 5546445.0
loss of iteration 46608: 5546444.0
loss of iteration 46609: 5546443.5
loss of iteration 46610: 5546442.0
loss of iteration 46611: 5546441.0
loss of iteration 46612: 5546440.5
loss of iteration 46613: 5546439.5
loss of iteration 46614: 5546437.5
loss of iteration 46615: 5546437.0
loss of iteration 46616: 5546436.5
loss of iteration 46617: 5546435.5
loss of iteration 46618: 5546434.5
loss of iteration 46619: 5546433.5
loss of iteration 46620: 5546432.0
loss of iteration 46

loss of iteration 47397: 5545695.0
loss of iteration 47398: 5545694.0
loss of iteration 47399: 5545692.5
loss of iteration 47400: 5545692.5
loss of iteration 47401: 5545691.0
loss of iteration 47402: 5545689.5
loss of iteration 47403: 5545689.5
loss of iteration 47404: 5545688.5
loss of iteration 47405: 5545687.0
loss of iteration 47406: 5545687.0
loss of iteration 47407: 5545686.0
loss of iteration 47408: 5545685.0
loss of iteration 47409: 5545684.0
loss of iteration 47410: 5545682.0
loss of iteration 47411: 5545682.0
loss of iteration 47412: 5545680.0
loss of iteration 47413: 5545680.0
loss of iteration 47414: 5545678.0
loss of iteration 47415: 5545677.5
loss of iteration 47416: 5545677.0
loss of iteration 47417: 5545676.0
loss of iteration 47418: 5545676.0
loss of iteration 47419: 5545673.5
loss of iteration 47420: 5545673.0
loss of iteration 47421: 5545672.5
loss of iteration 47422: 5545671.5
loss of iteration 47423: 5545670.0
loss of iteration 47424: 5545669.5
loss of iteration 47

loss of iteration 48181: 5544957.5
loss of iteration 48182: 5544956.5
loss of iteration 48183: 5544956.5
loss of iteration 48184: 5544956.0
loss of iteration 48185: 5544953.5
loss of iteration 48186: 5544953.0
loss of iteration 48187: 5544952.5
loss of iteration 48188: 5544951.5
loss of iteration 48189: 5544951.0
loss of iteration 48190: 5544949.0
loss of iteration 48191: 5544948.5
loss of iteration 48192: 5544947.0
loss of iteration 48193: 5544947.0
loss of iteration 48194: 5544946.5
loss of iteration 48195: 5544945.0
loss of iteration 48196: 5544944.0
loss of iteration 48197: 5544944.0
loss of iteration 48198: 5544942.0
loss of iteration 48199: 5544941.0
loss of iteration 48200: 5544940.0
loss of iteration 48201: 5544939.5
loss of iteration 48202: 5544939.0
loss of iteration 48203: 5544937.5
loss of iteration 48204: 5544937.0
loss of iteration 48205: 5544935.5
loss of iteration 48206: 5544935.0
loss of iteration 48207: 5544933.5
loss of iteration 48208: 5544932.5
loss of iteration 48

loss of iteration 48889: 5544299.0
loss of iteration 48890: 5544298.0
loss of iteration 48891: 5544297.5
loss of iteration 48892: 5544296.0
loss of iteration 48893: 5544295.0
loss of iteration 48894: 5544294.0
loss of iteration 48895: 5544294.0
loss of iteration 48896: 5544293.5
loss of iteration 48897: 5544292.0
loss of iteration 48898: 5544291.0
loss of iteration 48899: 5544291.0
loss of iteration 48900: 5544289.5
loss of iteration 48901: 5544288.0
loss of iteration 48902: 5544287.5
loss of iteration 48903: 5544286.5
loss of iteration 48904: 5544286.0
loss of iteration 48905: 5544284.0
loss of iteration 48906: 5544283.5
loss of iteration 48907: 5544282.5
loss of iteration 48908: 5544282.0
loss of iteration 48909: 5544280.0
loss of iteration 48910: 5544280.0
loss of iteration 48911: 5544278.5
loss of iteration 48912: 5544278.5
loss of iteration 48913: 5544277.0
loss of iteration 48914: 5544275.5
loss of iteration 48915: 5544275.0
loss of iteration 48916: 5544274.5
loss of iteration 48

loss of iteration 49699: 5543551.5
loss of iteration 49700: 5543550.5
loss of iteration 49701: 5543549.0
loss of iteration 49702: 5543549.0
loss of iteration 49703: 5543547.5
loss of iteration 49704: 5543546.5
loss of iteration 49705: 5543546.0
loss of iteration 49706: 5543545.0
loss of iteration 49707: 5543544.5
loss of iteration 49708: 5543543.0
loss of iteration 49709: 5543541.5
loss of iteration 49710: 5543542.0
loss of iteration 49711: 5543540.5
loss of iteration 49712: 5543539.0
loss of iteration 49713: 5543539.0
loss of iteration 49714: 5543537.5
loss of iteration 49715: 5543537.0
loss of iteration 49716: 5543536.5
loss of iteration 49717: 5543535.0
loss of iteration 49718: 5543534.0
loss of iteration 49719: 5543533.0
loss of iteration 49720: 5543532.0
loss of iteration 49721: 5543531.5
loss of iteration 49722: 5543530.0
loss of iteration 49723: 5543529.0
loss of iteration 49724: 5543527.5
loss of iteration 49725: 5543527.5
loss of iteration 49726: 5543526.0
loss of iteration 49

In [8]:
from pytorch_lightning.metrics.functional import r2score

# Must convert from np.array to torch.tensor 
test_inputs = torch.from_numpy(X_test).float()
test_labels = torch.from_numpy(Y_test).float()

# Sets model to evaluation mode. Evaluation mode turns off
# certain layers such as dropout or batch-norm, as these
# behave differently while training.
model.eval()

# predict and print r2 score
with torch.no_grad():
    test_pred = model(test_inputs)
    r2 = r2score(test_pred, test_labels)
    print(r2.item())

0.6448399424552917


### Observations

Our first attempt at training a linear regression model provided us with a few observations to note. First is that the loss is huge, even after gradient descent. This is because we are working with huge labels and our output space is very large, so do not be alarmed by the loss. It is better to note the R2 score, which our first model achieved 74%, which is fairly good. Lets fill in the observation table:

| Model | observations | R2 |
| :---- | :----------- | :--- |
| Multi-variate Linear Regerssion | Very large cost, used a very small learning rate | 74% |


## Prototyping Our Second Model (Polynomial Regression)

We are going to train a second model, this time using polynomial regression with cubic features. This in theory should be able to fit a more complicated function to the data.

In [9]:
poly = PolynomialFeatures(degree=3)

# convert to polynomial features
X_train_p = poly.fit_transform(X_train)
X_test_p = poly.fit_transform(X_test)
Y_train_p = Y_train
Y_test_p = Y_test

print(f"X_train_p shape: {X_train_p.shape}")
print(f"Y_train_p shape: {Y_train_p.shape}")
print(f"X_test_p shape: {X_test_p.shape}")
print(f"Y_test_p shape: {Y_test_p.shape}")

X_train_p shape: (447, 35)
Y_train_p shape: (447, 1)
X_test_p shape: (50, 35)
Y_test_p shape: (50, 1)


In [10]:
# batch norm is used to normalize the inputs. Don't worry about 
# Explaining this to students, as it will be covered in a later topic
from torch.nn import BatchNorm1d

class Linreg_p(Module):
    def __init__(self, inputs, outputs):
        super().__init__()
        self.linear = Linear(inputs, outputs) 
        self.bn = BatchNorm1d(inputs)
        
    def forward(self, x):
        x = self.bn(x)
        y_pred = self.linear(x)
        return y_pred

In [11]:
input_dims_p, output_dims_p = (X_train_p.shape[1], Y_train_p.shape[1])
learning_rate_p = 0.000001
epochs_p = 50000

In [12]:
model_p = Linreg_p(input_dims_p, output_dims_p)

# Optimizer and loss
optimizer_p = SGD(model_p.parameters(), lr=learning_rate_p)
loss_p = MSELoss()

In [13]:
# Convert to torch.tensor
inputs_p = torch.from_numpy(X_train_p).float()
labels_p = torch.from_numpy(Y_train_p).float()

if __name__ == "__main__":
    for i in range(epochs_p):
        
        # removes gradients from previous iteration
        model_p.zero_grad()
        # Feed Forward
        pred_p = model_p(inputs_p)
        # calculate cost
        errors_p = loss(pred_p, labels_p)
        print(f"loss of iteration {i+1}: {errors_p}")
        # Backpropagation
        errors_p.backward()
        # Update parameters
        optimizer_p.step()
    

loss of iteration 1: 39944780.0
loss of iteration 2: 39943544.0
loss of iteration 3: 39942308.0
loss of iteration 4: 39941068.0
loss of iteration 5: 39939832.0
loss of iteration 6: 39938592.0
loss of iteration 7: 39937352.0
loss of iteration 8: 39936108.0
loss of iteration 9: 39934864.0
loss of iteration 10: 39933612.0
loss of iteration 11: 39932364.0
loss of iteration 12: 39931108.0
loss of iteration 13: 39929844.0
loss of iteration 14: 39928576.0
loss of iteration 15: 39927308.0
loss of iteration 16: 39926032.0
loss of iteration 17: 39924748.0
loss of iteration 18: 39923456.0
loss of iteration 19: 39922156.0
loss of iteration 20: 39920848.0
loss of iteration 21: 39919532.0
loss of iteration 22: 39918208.0
loss of iteration 23: 39916876.0
loss of iteration 24: 39915532.0
loss of iteration 25: 39914184.0
loss of iteration 26: 39912812.0
loss of iteration 27: 39911432.0
loss of iteration 28: 39910048.0
loss of iteration 29: 39908652.0
loss of iteration 30: 39907236.0
loss of iteration 3

loss of iteration 307: 29710862.0
loss of iteration 308: 29555648.0
loss of iteration 309: 29398976.0
loss of iteration 310: 29240884.0
loss of iteration 311: 29081364.0
loss of iteration 312: 28920458.0
loss of iteration 313: 28758172.0
loss of iteration 314: 28594534.0
loss of iteration 315: 28429560.0
loss of iteration 316: 28263276.0
loss of iteration 317: 28095702.0
loss of iteration 318: 27926874.0
loss of iteration 319: 27756808.0
loss of iteration 320: 27585538.0
loss of iteration 321: 27413090.0
loss of iteration 322: 27239496.0
loss of iteration 323: 27064782.0
loss of iteration 324: 26888986.0
loss of iteration 325: 26712142.0
loss of iteration 326: 26534280.0
loss of iteration 327: 26355434.0
loss of iteration 328: 26175652.0
loss of iteration 329: 25994958.0
loss of iteration 330: 25813398.0
loss of iteration 331: 25631014.0
loss of iteration 332: 25447844.0
loss of iteration 333: 25263926.0
loss of iteration 334: 25079306.0
loss of iteration 335: 24894032.0
loss of iterat

loss of iteration 670: 7316795.0
loss of iteration 671: 7312146.0
loss of iteration 672: 7307505.5
loss of iteration 673: 7302877.5
loss of iteration 674: 7298259.0
loss of iteration 675: 7293650.0
loss of iteration 676: 7289051.5
loss of iteration 677: 7284460.0
loss of iteration 678: 7279880.5
loss of iteration 679: 7275310.5
loss of iteration 680: 7270750.0
loss of iteration 681: 7266199.0
loss of iteration 682: 7261657.5
loss of iteration 683: 7257127.0
loss of iteration 684: 7252604.5
loss of iteration 685: 7248092.5
loss of iteration 686: 7243588.5
loss of iteration 687: 7239094.5
loss of iteration 688: 7234610.0
loss of iteration 689: 7230136.5
loss of iteration 690: 7225670.5
loss of iteration 691: 7221215.0
loss of iteration 692: 7216768.5
loss of iteration 693: 7212330.0
loss of iteration 694: 7207903.5
loss of iteration 695: 7203481.5
loss of iteration 696: 7199073.0
loss of iteration 697: 7194672.0
loss of iteration 698: 7190280.5
loss of iteration 699: 7185898.0
loss of it

loss of iteration 1011: 6177457.0
loss of iteration 1012: 6175138.5
loss of iteration 1013: 6172824.0
loss of iteration 1014: 6170513.0
loss of iteration 1015: 6168206.5
loss of iteration 1016: 6165905.5
loss of iteration 1017: 6163607.0
loss of iteration 1018: 6161315.0
loss of iteration 1019: 6159025.0
loss of iteration 1020: 6156741.5
loss of iteration 1021: 6154460.0
loss of iteration 1022: 6152183.0
loss of iteration 1023: 6149912.0
loss of iteration 1024: 6147644.5
loss of iteration 1025: 6145381.0
loss of iteration 1026: 6143121.5
loss of iteration 1027: 6140866.0
loss of iteration 1028: 6138614.5
loss of iteration 1029: 6136368.5
loss of iteration 1030: 6134125.0
loss of iteration 1031: 6131886.0
loss of iteration 1032: 6129652.0
loss of iteration 1033: 6127419.5
loss of iteration 1034: 6125194.0
loss of iteration 1035: 6122971.0
loss of iteration 1036: 6120752.0
loss of iteration 1037: 6118537.5
loss of iteration 1038: 6116327.0
loss of iteration 1039: 6114120.0
loss of iterat

loss of iteration 1316: 5612198.0
loss of iteration 1317: 5610639.0
loss of iteration 1318: 5609081.5
loss of iteration 1319: 5607524.0
loss of iteration 1320: 5605968.0
loss of iteration 1321: 5604412.5
loss of iteration 1322: 5602857.0
loss of iteration 1323: 5601305.0
loss of iteration 1324: 5599752.0
loss of iteration 1325: 5598201.0
loss of iteration 1326: 5596650.0
loss of iteration 1327: 5595099.5
loss of iteration 1328: 5593549.5
loss of iteration 1329: 5592002.5
loss of iteration 1330: 5590455.5
loss of iteration 1331: 5588909.0
loss of iteration 1332: 5587363.0
loss of iteration 1333: 5585818.0
loss of iteration 1334: 5584274.5
loss of iteration 1335: 5582730.0
loss of iteration 1336: 5581188.5
loss of iteration 1337: 5579647.0
loss of iteration 1338: 5578106.0
loss of iteration 1339: 5576566.0
loss of iteration 1340: 5575027.0
loss of iteration 1341: 5573489.0
loss of iteration 1342: 5571950.5
loss of iteration 1343: 5570414.5
loss of iteration 1344: 5568877.5
loss of iterat

...

loss of iteration 48398: 1997530.25
loss of iteration 48399: 1997517.5
loss of iteration 48400: 1997505.625
loss of iteration 48401: 1997493.875
loss of iteration 48402: 1997482.125
loss of iteration 48403: 1997469.625
loss of iteration 48404: 1997457.5
loss of iteration 48405: 1997445.25
loss of iteration 48406: 1997434.25
loss of iteration 48407: 1997421.0
loss of iteration 48408: 1997409.625
loss of iteration 48409: 1997398.0
loss of iteration 48410: 1997385.125
loss of iteration 48411: 1997372.625
loss of iteration 48412: 1997361.125
loss of iteration 48413: 1997348.75
loss of iteration 48414: 1997336.875
loss of iteration 48415: 1997324.625
loss of iteration 48416: 1997313.0
loss of iteration 48417: 1997300.5
loss of iteration 48418: 1997288.75
loss of iteration 48419: 1997276.75
loss of iteration 48420: 1997264.5
loss of iteration 48421: 1997252.0
loss of iteration 48422: 1997240.125
loss of iteration 48423: 1997228.125
loss of iteration 48424: 1997216.375
loss of iteration 48425

loss of iteration 48737: 1993465.0
loss of iteration 48738: 1993453.625
loss of iteration 48739: 1993441.375
loss of iteration 48740: 1993429.375
loss of iteration 48741: 1993418.125
loss of iteration 48742: 1993405.875
loss of iteration 48743: 1993394.375
loss of iteration 48744: 1993381.75
loss of iteration 48745: 1993370.25
loss of iteration 48746: 1993358.125
loss of iteration 48747: 1993346.625
loss of iteration 48748: 1993334.5
loss of iteration 48749: 1993322.5
loss of iteration 48750: 1993310.5
loss of iteration 48751: 1993298.625
loss of iteration 48752: 1993287.0
loss of iteration 48753: 1993274.75
loss of iteration 48754: 1993262.875
loss of iteration 48755: 1993250.875
loss of iteration 48756: 1993239.75
loss of iteration 48757: 1993227.25
loss of iteration 48758: 1993215.75
loss of iteration 48759: 1993203.5
loss of iteration 48760: 1993191.25
loss of iteration 48761: 1993180.25
loss of iteration 48762: 1993167.75
loss of iteration 48763: 1993156.0
loss of iteration 48764:

loss of iteration 49051: 1989755.125
loss of iteration 49052: 1989742.625
loss of iteration 49053: 1989731.125
loss of iteration 49054: 1989719.5
loss of iteration 49055: 1989707.625
loss of iteration 49056: 1989695.75
loss of iteration 49057: 1989684.125
loss of iteration 49058: 1989672.5
loss of iteration 49059: 1989660.625
loss of iteration 49060: 1989648.875
loss of iteration 49061: 1989637.25
loss of iteration 49062: 1989625.125
loss of iteration 49063: 1989614.25
loss of iteration 49064: 1989602.25
loss of iteration 49065: 1989590.375
loss of iteration 49066: 1989578.875
loss of iteration 49067: 1989567.0
loss of iteration 49068: 1989555.25
loss of iteration 49069: 1989543.5
loss of iteration 49070: 1989531.75
loss of iteration 49071: 1989520.625
loss of iteration 49072: 1989508.125
loss of iteration 49073: 1989496.5
loss of iteration 49074: 1989484.875
loss of iteration 49075: 1989473.375
loss of iteration 49076: 1989461.25
loss of iteration 49077: 1989449.625
loss of iteration 

loss of iteration 49381: 1985914.0
loss of iteration 49382: 1985902.375
loss of iteration 49383: 1985890.25
loss of iteration 49384: 1985878.75
loss of iteration 49385: 1985867.625
loss of iteration 49386: 1985855.875
loss of iteration 49387: 1985844.375
loss of iteration 49388: 1985833.125
loss of iteration 49389: 1985821.75
loss of iteration 49390: 1985809.75
loss of iteration 49391: 1985798.125
loss of iteration 49392: 1985786.5
loss of iteration 49393: 1985775.0
loss of iteration 49394: 1985763.625
loss of iteration 49395: 1985752.375
loss of iteration 49396: 1985740.625
loss of iteration 49397: 1985729.0
loss of iteration 49398: 1985717.375
loss of iteration 49399: 1985706.125
loss of iteration 49400: 1985694.375
loss of iteration 49401: 1985682.625
loss of iteration 49402: 1985671.0
loss of iteration 49403: 1985659.375
loss of iteration 49404: 1985648.125
loss of iteration 49405: 1985636.25
loss of iteration 49406: 1985625.625
loss of iteration 49407: 1985613.875
loss of iteratio

loss of iteration 49741: 1981793.875
loss of iteration 49742: 1981781.875
loss of iteration 49743: 1981770.875
loss of iteration 49744: 1981759.875
loss of iteration 49745: 1981748.5
loss of iteration 49746: 1981737.0
loss of iteration 49747: 1981725.875
loss of iteration 49748: 1981714.375
loss of iteration 49749: 1981703.125
loss of iteration 49750: 1981691.875
loss of iteration 49751: 1981680.25
loss of iteration 49752: 1981668.75
loss of iteration 49753: 1981657.875
loss of iteration 49754: 1981646.125
loss of iteration 49755: 1981635.125
loss of iteration 49756: 1981624.125
loss of iteration 49757: 1981612.375
loss of iteration 49758: 1981601.25
loss of iteration 49759: 1981589.625
loss of iteration 49760: 1981577.75
loss of iteration 49761: 1981567.125
loss of iteration 49762: 1981555.375
loss of iteration 49763: 1981544.25
loss of iteration 49764: 1981533.125
loss of iteration 49765: 1981521.625
loss of iteration 49766: 1981510.25
loss of iteration 49767: 1981499.0
loss of itera

In [14]:
# Convert to torch.tensor
test_inputs_p = torch.from_numpy(X_test_p).float()
test_labels_p = torch.from_numpy(Y_test_p).float()

# Eval mode
model_p.eval()

#predict and print r2
with torch.no_grad():
    test_pred_p = model_p(test_inputs_p)
    r2_p = r2score(test_pred_p, test_labels_p)
    print(r2_p.item())

0.9556198716163635


This looks even better! I think this model is ready for use. Before we save the model, lets record the observations in the table below:

| Model | observations | R2 |
| :---- | :----------- | :--- |
| Multi-variate Linear Regerssion | Very large cost, used a very small learning rate | 74% |
| Polynomial Regression | Cost is smaller but still large. This is no issue | 93% |

In [15]:
if __name__ == "__main__":
    torch.save(model_p.state_dict(), "gpu-predictor.pt")

## References

1. https://www.alliedmarketresearch.com/graphic-processing-unit-market
2. https://pytorch.org/docs/stable/generated/torch.nn.Module.html#torch.nn.Module